# Principle Component Analysis

Author: [Pili Hu](http://hupili.net)
    
Let's try to visualize the legco data set via dimensionality reduction.
We only show PCA in this notebook.
If you are interested in more dimensionality reduction techniques, please find pointers in reference section.



## Principal Component Analysis


In [20]:
#file_prefix = 'https://course.ie.cuhk.edu.hk/~engg4030/tutorial/tutorial7/'
file_prefix = ''
import pandas as pd
df = pd.io.parsers.read_csv(file_prefix + 'votes-matrix.csv', index_col='member')
df[:5]

20121017-1 20121017-10 20121017-2 20121017-3 20121017-4  \
member                                                                 
Abraham SHEK         No          No         No         No         No   
Alan LEONG          Yes         Yes        Yes        Yes        Yes   
Albert CHAN         Yes         Yes        Yes        Yes        Yes   
Albert HO           Yes         Yes        Yes        Yes        Yes   
Alice MAK            No         Yes         No         No        Yes   

             20121017-5 20121017-6 20121017-7 20121017-8 20121017-9  \
member                                                                
Abraham SHEK         No         No         No         No         No   
Alan LEONG          Yes        Yes         No         No         No   
Albert CHAN         Yes    Abstain         No         No         No   
Albert HO           Yes        Yes         No         No         No   
Alice MAK           Yes    Abstain         No         No    Abstain   

                ...     20140219-2 20140219-20 20140219-21 20140219-3  \
member          ...                                                     
Abraham SHEK    ...        Abstain         Yes          No         No   
Alan LEONG      ...        Abstain         Yes      Absent         No   
Albert CHAN     ...             No      Absent     Abstain     Absent   
Albert HO       ...            Yes         Yes      Absent         No   
Alice MAK       ...            Yes         Yes         Yes         No   

             20140219-4 20140219-5 20140219-6 20140219-7 20140219-8 20140219-9  
member                                                                          
Abraham SHEK        Yes        Yes        Yes         No     Absent    Abstain  
Alan LEONG           No         No        Yes        Yes        Yes     Absent  
Albert CHAN          No        Yes        Yes        Yes     Absent     Absent  
Albert HO            No        Yes        Yes        Yes        Yes        Yes  
Alice MAK            No         No         No        Yes         No         No  

[5 rows x 1031 columns]

In [21]:
X = df.as_matrix()
# This is member-by-vote matrix
print X.shape
# A corner of the matrix
print X[:5, :5]

(70, 1031)
[['No' 'No' 'No' 'No' 'No']
 ['Yes' 'Yes' 'Yes' 'Yes' 'Yes']
 ['Yes' 'Yes' 'Yes' 'Yes' 'Yes']
 ['Yes' 'Yes' 'Yes' 'Yes' 'Yes']
 ['No' 'Yes' 'No' 'No' 'Yes']]


In [22]:
# Convert string value to numeric value
X[(X!='Yes') & (X!='No')] = 0
X[X=='Yes'] = 1
X[X=='No'] = -1
X = matrix(X.astype('float'))

According to one friend, the meaning of labels are as follows:

   * Yes: Yes
   * No: No
   * Absent: Did not come
   * Abstain: Did not vote
   * Present: Came at first, but was abset when vote this topic
   
Correct if the interpretation is wrong.
For the educational purpose, we simply give anything other than "Yes" or "No" a value `0`.


In [23]:
# Check whether all cells are transformed to numerical values.
print len(find(X == -1))
print len(find(X == 1))
print len(find(X == 0))
print len(find(X == -1)) + len(find(X == 0)) + len(find(X == 1))
print size(X)
print X[:5, :5]

28471
10939
32760
72170
72170
[[-1. -1. -1. -1. -1.]
 [ 1.  1.  1.  1.  1.]
 [ 1.  1.  1.  1.  1.]
 [ 1.  1.  1.  1.  1.]
 [-1.  1. -1. -1.  1.]]


In [24]:
# Centering!
# This is a often neglectd step!
# If you wonder what happens without centering, see the remarks section
X = X - mean(X, 0)
print X[:5, :5]

[[-0.8        -1.24285714 -0.78571429 -0.8        -1.21428571]
 [ 1.2         0.75714286  1.21428571  1.2         0.78571429]
 [ 1.2         0.75714286  1.21428571  1.2         0.78571429]
 [ 1.2         0.75714286  1.21428571  1.2         0.78571429]
 [-0.8         0.75714286 -0.78571429 -0.8         0.78571429]]


In [25]:
# The covariance matrix
C = X.T * X
print C.shape

(1031, 1031)


In [44]:
# EVD and get Principle **Axis**
# In previous version of this note, we use eig to get all eigen values/vectors.
# It suffers from compatibility problems and is inefficient on large matrix.
# scipy.sparse.linalg.eigs is a more advanced interface to get partial eigen values/vectors.
import scipy.sparse.linalg
PA = scipy.sparse.linalg.eigs(C, k=2, which='LM', return_eigenvectors=True)[1]

# Project data points onto principle axis
X_2D = PA.T * X.T
print X_2D.shape
x = array(X_2D[0, :]).astype('float')
y = array(X_2D[1, :]).astype('float')
scatter(x, y)

(2, 70)


/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: ComplexWarning: Casting complex values to real discards the imaginary part
/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: ComplexWarning: Casting complex values to real discards the imaginary part


In [39]:
# Use the following one to pop up the 3D plot in another window.
# Good for interactive exploration.
# May or may not be available due to your desktop.
%pylab
# Use the following one to plot inline (embedded in this notebook).
#%pylab inline

# Try 3D
PA = scipy.sparse.linalg.eigs(C, k=3, which='LM', return_eigenvectors=True)[1]
# Project data points onto principle axis
X_3D = PA.T * X.T
print X_3D.shape
# We intentionally add some disturbance for better visualization.
# Or else, some of the nodes are located in the same place.
# (Those who vote exactly the same)
X_3D = X_3D + randn(*tuple(X_3D.shape)) * 0.3
x = array(X_3D[0, :]).astype('float')
y = array(X_3D[1, :]).astype('float')
z = array(X_3D[2, :]).astype('float')

from mpl_toolkits.mplot3d import Axes3D
fig = figure()
ax = fig.add_subplot(111, projection='3d')
ax.scatter(x, y, z, picker=True, s=100)
title('HK Legco 2012.10 ~ 2015.6 Votes (3 PCs)')
ax.set_xlabel('Principal Component 1')
ax.set_ylabel('Principal Component 2')
ax.set_zlabel('Principal Component 3')

def onpick(event):
    if hasattr(onpick, '_label'):
        #pass
        onpick._label.remove()
    thisline = event.artist
    ind = event.ind
    #print type(ind)
    #print X_3D[0, ind]
    names = df.iloc[ind].index.values
    label = ('\n'.join(names))
    pos = (X_3D[0, ind[0]], X_3D[1, ind[0]], X_3D[2, ind[0]])
    #onpick._label = ax.set_title(label
    onpick._label = ax.text(*pos, s=label)
    fig.canvas.draw()
    
fig.canvas.mpl_connect('pick_event', onpick)

Using matplotlib backend: MacOSX
Populating the interactive namespace from numpy and matplotlib
(3, 70)


/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:17: ComplexWarning: Casting complex values to real discards the imaginary part
/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:18: ComplexWarning: Casting complex values to real discards the imaginary part
/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:19: ComplexWarning: Casting complex values to real discards the imaginary part


9

You can change "%pylab inline" to "%pylab"i n the above cell to pop the 3D plot in another window.
Pick some points and you can see who are those people.
You can also zoom/pan/rotate the plot to explore in details.
Following is one example:

In [28]:
from IPython.display import Image
Image(url=(file_prefix + 'screen-legco-pca-3d-labels.png'))

**EXERCISE**:
We have used PCA to visualize **what members vote alike**.
Try to visualize **what topics are voted alike**.
You may try the following two methods:

   * Simply transpose the original data matrix $X$, and do the same numeric computation.
   * Re-use the above l ($[\lambda_1,\ldots,\lambda_n]$) and U ($[U_1,\ldots,U_n]$).
   Compute what you need (principle axis, principle component) by matrix multiplication, instead of decomposition.

I strongly encourage you to try both methods.
By deriving the math relation between $U,V,\Lambda,\Sigma$, you will get a deeper understanding.

## The energy (optional)

What's the energy preserved by principal axes?
i.e. sum of squared singular values or sum of eigen values.
In a previous version of this note, we use `eig` to get all eigen values.
Now we only get the largest eigen values.
Without a full decomposition, what can we do?

Recall the [trace](http://en.wikipedia.org/wiki/Trace_%28linear_algebra%29) you learned in linear algebra:

$$Tr[X] = Tr[U \Lambda U^T] = Tr[U^T U \Lambda] = Tr[\Lambda]$$

So the sum of diagonal is equal to the sum of eigen values.
We can use this to compute the percentage of captured energy by principal axes.

In [29]:
l = scipy.sparse.linalg.eigs(C, k=5, which='LM', return_eigenvectors=False)
for i in l:
    print 'eval=', float(i), '%=', float(i) / trace(C)

eval= 614.335088097 %= 0.022421479598
eval= 631.805969672 %= 0.023059116976
eval= 1035.41967009 %= 0.0377898665697
eval= 1868.59401075 %= 0.0681983551007
eval= 15788.2125691 %= 0.576224755619


/Users/hupili/Desktop/initium/hk_legco/third/hupili-engg4030/src/t7-pca/venv/lib/python2.7/site-packages/IPython/kernel/__main__.py:3: ComplexWarning: Casting complex values to real discards the imaginary part
  app.launch_new_instance()


Only ~70% is captured by first three principal axes.

## Remarks (optional)
   
Mis-uses/mis-interpretations of PCA:
   
   * What happens without centering?
   You can directly decompose the matrix without centering.
   It still gives you certain good visualization.
   Note that it is not PCA anymore!
   However, it is a valid spectral embedding technique (see reference).
   * Principal component and principal axis.
   Depending on the convention of $X$ (row is data point or column is data point), the interpretation of $U$ and $V$ are different.
   Besides, "principal component" is used for "principal axis" in some texts.
   We adopt the following convention: ($n$ data points; reduce from $d$ dimension to $k$ dimension)
      * Principal axes: They are $k$ $d$-dimensional vectors.
      i.e. they are in the original space. 
      i.e. they span a subspace in the original space.
      * Principal components: They are $n$ $k$-dimensional vectors.
      i.e. they are the coordinates of original data points in the new dimension-reduced space.
   * Suppose data points are organized in columns.
   Given $X=U\Sigma V^T$ (e.g. by decomposing $X X^T$), we truncate to the large $k$ singular values: $X \approx U_k\Sigma_k V_k^T$
   We know that $ U_k$ is principal axis and $\Sigma_k V_k^T$ is the principal component.
   We need to plot $\Sigma_k V_k^T$ to get a lower dimension embedding.
   However, people sometimes decompose $X^T X$ to obtain $V_k^T$ and plot it direclty.
   $V_k^T$ and $\Sigma_k V_k^T$ are of same dimension, so there is no problem.
   Again, this is not PCA but it is within the scope of spectral embedding techniques and gives nice visualization sometimes.

How to interpret the above "Mis-uses/mis-interpretations"?
It is here to remind you that there are rigorous math formulations and derivations behind PCA.
It is very easy to mis-use the algorithm and mis-interpret the result.
However, it does not say the variants are incorrect.
On the contrary, PCA is not ideal in many cases and the variants turn out to be useful sometimes.
Some of the variants also have rigorous math justifications but some of them do not have.
Some of them have been formalized and named but some are not.
It is very common to see people get "right result" using "wrong method".
Just stay open-mineded.
In the world of data mining, there are no one-size-fit-all strong algorithms but there are strong miners.
**Pre-processing** and **post-processing** may sometimes be even more important than the algorithm.

## References

   * Lecture notes _Dimensionality Reduction Part 1_ : https://course.ie.cuhk.edu.hk/~engg4030/lecture/Dimension1.pdf
   * **Jolliffe, Ian.** _Principal component analysis_. John Wiley & Sons, Ltd, 2005. APA.
   * PCA is just one of the many **spectral** dimensionality reduction methods.
   If you want to explore more, you can refer to my
   [notes on spectral clustering](http://project.hupili.net/tutorial/hu2012-spectral/hu2012-spectral.html).
      * The [techreport](http://project.hupili.net/tutorial/hu2012-spectral/hu2012spectral-survey.pdf) 
      surveys some common linear and non-linear DR methods.
      * The [slides, p21-26](http://project.hupili.net/tutorial/hu2012-spectral/hu2013spectral-slides.pdf) 
      has a quick overview of PCA from formulation to some operational nitty-gritties (e.g. principle component v.s. principle axis).
   * PCA (and spectral embedding methods) may not be the best way to visualize this data set.
   Given the voting matrix, one can extract a "social graph" on legco members.
   [Force-directed layout](http://en.wikipedia.org/wiki/Force-directed_graph_drawing)
   is a popular family of methods to visualize this type of data.
   (depending on time availability, this may be covered during graph mining chapters)